In [1]:
import pandas as pd
import numpy as np
import re
import string
import nltk
from nltk.corpus import stopwords
import sklearn 
from nltk.tokenize import word_tokenize
import warnings
warnings.filterwarnings('ignore')

In [2]:
data = pd.read_csv('/content/df_47k - Sheet1.csv')  
data.head()

Unnamed: 0  Unnamed: 0.1  \
0           0             0   
1           1             1   
2           2             2   
3           3             3   
4           4             4   

                                                text         Username  \
0  بشرى سارة لجماهير النادي الأهلي \nللتفاصيل htt...        Al3hdNews   
1  @SXANJI لا احب الأنميات الرياضية يكفي اني اتاب...     fekrytarro22   
2  RT @kdzh37: الفتى الذهبي ⭐️ يعلن الاكتفاء ويضع...          hmde441   
3  RT @KSA24: يسألون \nليه #مقاطعة_البضائع_التركي...  saefAlJohaniksa   
4  RT @Ahmed08911311: يوميا صفحه من القرآن \nكفيل...           wabil_   

                        Timestamp  followers  label categorie  
0  Sat Oct 10 19:41:00 +0000 2020          4      0     sport  
1  Thu Oct 08 20:10:28 +0000 2020        365      0     sport  
2  Fri Oct 09 20:55:46 +0000 2020       1663      0     sport  
3  Tue Oct 13 01:38:17 +0000 2020        443      4   economy  
4  Sat Oct 10 21:27:14 +0000 2020       5873      2  religion

In [3]:
data = data.take(np.random.permutation(len(data))[:])

In [4]:
data.shape

(47083, 8)

In [5]:
data.isna().sum()

Unnamed: 0      0
Unnamed: 0.1    0
text            0
Username        0
Timestamp       0
followers       0
label           0
categorie       0
dtype: int64

In [6]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 47083 entries, 36557 to 33383
Data columns (total 8 columns):
 #   Column        Non-Null Count  Dtype 
---  ------        --------------  ----- 
 0   Unnamed: 0    47083 non-null  int64 
 1   Unnamed: 0.1  47083 non-null  int64 
 2   text          47083 non-null  object
 3   Username      47083 non-null  object
 4   Timestamp     47083 non-null  object
 5   followers     47083 non-null  int64 
 6   label         47083 non-null  int64 
 7   categorie     47083 non-null  object
dtypes: int64(4), object(4)
memory usage: 3.2+ MB


In [7]:
# Arabic letters encodings

COMMA = u'\u060C'
SEMICOLON = u'\u061B'
QUESTION = u'\u061F'
HAMZA = u'\u0621'
ALEF_MADDA = u'\u0622'
ALEF_HAMZA_ABOVE = u'\u0623'
WAW_HAMZA = u'\u0624'
ALEF_HAMZA_BELOW = u'\u0625'
YEH_HAMZA = u'\u0626'
ALEF = u'\u0627'
TEH_MARBUTA = u'\u0629'
TATWEEL = u'\u0640'
LAM = u'\u0644'
HEH = u'\u0647'
YEH = u'\u064a'
ALEF_MAKSURA = u'\u0649'
HAMZA_ABOVE = u'\u0654'
HAMZA_BELOW = u'\u0655'
PERCENT = u'\u066a'
DECIMAL = u'\u066b'
THOUSANDS = u'\u066c'
STAR = u'\u066d'
FULL_STOP = u'\u06d4'
BYTE_ORDER_MARK = u'\ufeff'
MULITIPLICATION_SIGN = u'\u00D7'
DIVISION_SIGN = u'\u00F7'


# Tashkeel
FATHATAN = u'\u064b'
DAMMATAN = u'\u064c'
KASRATAN = u'\u064d'
FATHA = u'\u064e'
DAMMA = u'\u064f'
KASRA = u'\u0650'
SHADDA = u'\u0651'
SUKUN = u'\u0652'

#Ligatures
LAM_ALEF = u'\ufefb'
LAM_ALEF_HAMZA_ABOVE = u'\ufef7'
LAM_ALEF_HAMZA_BELOW = u'\ufef9'
LAM_ALEF_MADDA_ABOVE = u'\ufef5'

HARAKAT_PAT = re.compile(u"["+u"".join([FATHATAN, DAMMATAN, KASRATAN, FATHA, DAMMA, KASRA, SUKUN, SHADDA])+u"]")
HAMZAT_PAT = re.compile(u"["+u"".join([WAW_HAMZA, YEH_HAMZA])+u"]")
ALEFAT_PAT = re.compile(u"["+u"".join([ALEF_MADDA, ALEF_HAMZA_ABOVE, ALEF_HAMZA_BELOW, HAMZA_ABOVE, HAMZA_BELOW])+u"]")
LAMALEFAT_PAT = re.compile(u"["+u"".join([LAM_ALEF, LAM_ALEF_HAMZA_ABOVE, LAM_ALEF_HAMZA_BELOW, LAM_ALEF_MADDA_ABOVE])+u"]")

WESTERN_ARABIC_NUMERALS = ['0','1','2','3','4','5','6','7','8','9']
EASTERN_ARABIC_NUMERALS = [u'\u06F0', u'\u06F1', u'\u06F2', u'\u06F3', u'\u0664', u'\u06F5', u'\u0666', u'\u06F7', u'\u06F8', u'\u06F9']

eastern_to_western_numerals = {}
for i in range(len(EASTERN_ARABIC_NUMERALS)):
    eastern_to_western_numerals[EASTERN_ARABIC_NUMERALS[i]] = WESTERN_ARABIC_NUMERALS[i]

arabic_punctuations = COMMA + SEMICOLON + QUESTION + PERCENT + DECIMAL + THOUSANDS + STAR + FULL_STOP + MULITIPLICATION_SIGN + DIVISION_SIGN
all_punctuations = string.punctuation + arabic_punctuations + '()[]{}' # English & Arabic punctuations

all_punctuations = ''.join(list(set(all_punctuations)))

In [8]:
def strip_tashkeel(text):
    text = HARAKAT_PAT.sub('', text)
    return text 

def strip_tatweel(text):
    return re.sub(u'[%s]' % TATWEEL, '', text)

def remove_non_arabic(text):
    return ' '.join(re.sub(u"[^\u0621-\u063A\u0640-\u0652 ]", " ", text,  flags=re.UNICODE).split())

def keep_arabic_english_n_symbols(text):
    return ' '.join(re.sub(u"[^\u0621-\u063A\u0640-\u064aa-zA-Z#@_:/ ]", "", text,  flags=re.UNICODE).split())

def normalize_hamza(text):
    text = ALEFAT_PAT.sub(ALEF, text)
    text = HAMZAT_PAT.sub(HAMZA, text)
    return text

def normalize_lamalef(text): 
    text = LAMALEFAT_PAT.sub((LAM, ALEF), text)
    return text

def normalize_spellerrors(text):
    text = re.sub(u'[%s]' % TEH_MARBUTA, HEH, text)
    return re.sub(u'[%s]' % ALEF_MAKSURA, YEH, text)

def remove_underscore(text):
    return ' '.join(text.split('_'))

def remove_retweet_tag(text):
    tag = re.compile('rt @[a-zA-Z0-9_]+:|@[a-zA-Z0-9_]+')
    text = tag.sub('', text)
    hashtag = re.compile('\#')
    text = hashtag.sub('', text)
    return text

def replace_emails(text):
    emails = re.findall(r'[\w\.-]+@[\w\.-]+', text)
    for email in emails:
        text = text.replace(email,'#')
    return text

def replace_urls(text):
    return re.sub(r"http\S+|www.\S+", "#", text)

def convert_eastern_to_western_numerals(text):
    for num in EASTERN_ARABIC_NUMERALS:
        text = text.replace(num, eastern_to_western_numerals[num])
    return text

def remove_all_punctuations(text):
    for punctuation in all_punctuations:
        text = text.replace(punctuation, ' ')
    return text

def remove_emojis(text):
    emoji_pattern = re.compile("["
        u"\U0001F600-\U0001F64F"  # emoticons
        u"\U0001F300-\U0001F5FF"  # symbols & pictographs
        u"\U0001F680-\U0001F6FF"  # transport & map symbols
        u"\U0001F1E0-\U0001F1FF"  # flags 
                           "]+", flags=re.UNICODE)
    text = emoji_pattern.sub('', text)
    return text

def replace_phone_numbers(text):
    return re.sub(r'\d{10}', '#', text)

def remove_extra_spaces(text):
    return ' '.join(text.split())

def normalize_tweet(text):
    new_text = text.lower()
    new_text = normalize_hamza(new_text)
    new_text = strip_tashkeel(new_text)
    new_text = strip_tatweel(new_text)
    new_text = normalize_spellerrors(new_text)
    new_text = remove_retweet_tag(new_text)
    new_text = replace_emails(new_text)
    new_text = remove_underscore(new_text)
    new_text = replace_phone_numbers(new_text)
    new_text = remove_all_punctuations(new_text)
    new_text = replace_urls(new_text)
    new_text = convert_eastern_to_western_numerals(new_text)
    new_text = keep_arabic_english_n_symbols(new_text)
    new_text = remove_non_arabic(new_text)
    new_text = remove_extra_spaces(new_text)
    
    return new_text

In [9]:
test= " لقد قال أنه يأكل لأنه يؤكل"

def normalize_hamza(text):
    text = ALEFAT_PAT.sub(ALEF,text)
    text = HAMZAT_PAT.sub(HAMZA,text)
    return text

result = normalize_hamza(test)
print(result)

 لقد قال انه ياكل لانه يءكل


In [10]:
data['text'] = data['text'].apply(normalize_tweet)
data.head()

Unnamed: 0  Unnamed: 0.1  \
36557       36557         36557   
566           566           566   
42845       42845         42845   
886           886           886   
17037       17037         17037   

                                                    text   Username  \
36557  لو الموسيقي تنحفظ في قلاده حفظت فيها اول دقيقه...   bodour69   
566    عاجل بمناسبه اليوم الوطني ال بالمملكه الحكومه ...      J7tm_   
42845  فان اكاونت اديل وتشين يقولان ويفوقان علي صناعه...  OreoBAEKY   
886    التصريحات كثيره والافعال قليله عجبي لمن يطالب ...     mkg_12   
17037  شريف العريان امين اللجنه الاولمبيه لعمرو اديب ...  AtefAbd73   

                            Timestamp  followers  label categorie  
36557  Thu Oct 08 21:30:06 +0000 2020        130      3       art  
566    Sat Oct 10 21:07:25 +0000 2020      35308      1   politic  
42845  Tue Oct 13 16:13:22 +0000 2020        167      3       art  
886    Fri Oct 09 21:50:10 +0000 2020       4277      1   politic  
17037  Fri Oct 09 20:47:27 +0000 2020       2164      0     sport

In [11]:
data['text'][5]

'فءه شيوخ الدين الي الله يكثر من امثالهم'

In [12]:
import nltk
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

In [13]:
# convert tweets col to one string
tweets = data.text.str.cat(sep=' ')
tweets

'لو الموسيقي تنحفظ في قلاده حفظت فيها اول دقيقه و عشرين ثانيه من هاالجمال الخالد عاجل بمناسبه اليوم الوطني ال بالمملكه الحكومه تصرف الف ريال لكل مواطن سعودي كنوع من انواع المساعده للمواطنين ع فان اكاونت اديل وتشين يقولان ويفوقان علي صناعه الموسيقي باكملها التصريحات كثيره والافعال قليله عجبي لمن يطالب بتطبيق القانون وهو لا يطبقه نصيحه لا تبلغ عن فساد كي لا تتورط فهناك م شريف العريان امين اللجنه الاولمبيه لعمرو اديب لا وزير الرياضه ولا القضاء ولا الكاف ولا الفيفا لهم اي سلطه لتغيير قر السينما مع شخص تحبه وربي احلي شي شراء اثاث مستعمل بالرياضدينا نقل عفش بالرياضشراء مكيفاتشراء ثلاجات شراء مطابخشراء شاشاتشراء غرف نومشراء معدات مطاعم حساب رسمي بيقول لرءيس الفيفا يلا مساكين ميعرفوش انه هو من يدير الكاف دلوقتي الله يرزقها وتبشر بالدعم بس حطي الاسعار وهل فيه انوع للقهوه احد يحبها ثقيله وفيه عشاق الشقرا وموالكل يحب كنيسه القيامه المسجد الاقصي عمر بن الخطاب وصلاح الدين الايوبي تاريخ عظيم معتصمو العلوم يستغيثونتتحمل الحكومه بكل اصنافها كل ما يتعرض له معتصمي العلوم من مخاطر ممكن ان تءدي بحياتهم بس

In [14]:
import nltk
from nltk.tokenize import word_tokenize

#function to split text into word
tokens = word_tokenize(tweets)

vocabulary = set(tokens)
print('no. of words is:', len(vocabulary))

frequency_dist = nltk.FreqDist(tokens) # words frequency
sorted(frequency_dist,key=frequency_dist.__getitem__, reverse=True)[0:20] # highest 20 word occurred only 

no. of words is: 66961


['في',
 'من',
 'علي',
 'و',
 'ان',
 'عن',
 'الله',
 'لا',
 'ما',
 'الرياضه',
 'الي',
 'الحكومه',
 'كل',
 'مع',
 'الدين',
 'التجاره',
 'الصلاه',
 'كره',
 'القدم',
 'وزاره']

In [15]:
import nltk
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


True

In [16]:
stop = stopwords.words('arabic')
arab_stopwords = set(nltk.corpus.stopwords.words("arabic"))
arab_stopwords

{'ء',
 'ءَ',
 'آ',
 'آب',
 'آذار',
 'آض',
 'آمينَ',
 'آناء',
 'آنفا',
 'آه',
 'آها',
 'آهاً',
 'آهٍ',
 'آهِ',
 'آي',
 'أ',
 'أبدا',
 'أبريل',
 'أبو',
 'أبٌ',
 'أجل',
 'أجمع',
 'أحد',
 'أخبر',
 'أخذ',
 'أخو',
 'أخٌ',
 'أربع',
 'أربعاء',
 'أربعة',
 'أربعمئة',
 'أربعمائة',
 'أرى',
 'أسكن',
 'أصبح',
 'أصلا',
 'أضحى',
 'أطعم',
 'أعطى',
 'أعلم',
 'أغسطس',
 'أف',
 'أفريل',
 'أفعل به',
 'أفٍّ',
 'أقبل',
 'أقل',
 'أكتوبر',
 'أكثر',
 'أل',
 'ألا',
 'ألف',
 'ألفى',
 'أم',
 'أما',
 'أمام',
 'أمامك',
 'أمامكَ',
 'أمد',
 'أمس',
 'أمسى',
 'أمّا',
 'أن',
 'أنا',
 'أنبأ',
 'أنت',
 'أنتم',
 'أنتما',
 'أنتن',
 'أنتِ',
 'أنشأ',
 'أنى',
 'أنًّ',
 'أنّى',
 'أهلا',
 'أو',
 'أوت',
 'أوشك',
 'أول',
 'أولئك',
 'أولاء',
 'أولالك',
 'أوه',
 'أوّهْ',
 'أى',
 'أي',
 'أيا',
 'أيار',
 'أيضا',
 'أيلول',
 'أين',
 'أينما',
 'أيها',
 'أيّ',
 'أيّان',
 'أُفٍّ',
 'ؤ',
 'إحدى',
 'إذ',
 'إذا',
 'إذاً',
 'إذما',
 'إذن',
 'إزاء',
 'إلا',
 'إلى',
 'إليك',
 'إليكم',
 'إليكما',
 'إليكن',
 'إليكنّ',
 'إليكَ',
 'إلَيْكَ',
 'إلّا',


In [17]:
arab_stopwords = '|'.join(arab_stopwords)
arab_stopwords

'كلّما|كلما|بَلْهَ|نَّ|إلّا|عين|ظلّ|لولا|هاك|شَتَّانَ|زاي|أينما|بس|إليكم|سوف|هيا|راح|لنا|لوما|ثمّة|هَذانِ|حبذا|اثنا|ليس|كذلك|ومن|كى|يورو|صهٍ|عيانا|هلا|أمس|اخلولق|ظنَّ|لمّا|إنه|فضلا|أعطى|واو|أوشك|خبَّر|طاء|ثلاثين|بها|نوفمبر|ستة|هيت|تشرين|عَدَسْ|مارس|تعلَّم|إذاً|مئة|قاطبة|أنتن|أف|لعل|عليه|لم|كاف|وإن|نيسان|حزيران|بؤسا|عاشر|في|إياكما|اللتان|ب|تموز|ث|هَذِه|كيت|إلى|وجد|إزاء|خلافا|حبيب|ريث|سبعمئة|جميع|اللتيا|ح|أى|الذين|اللواتي|علم|أخو|بهما|وا|تينك|هَاتِي|اتخذ|أنشأ|ولا|حيث|لدن|ذلكما|صبر|أول|مكانكم|دال|لدى|أنا|مايو|أمامك|أمامكَ|بخ|لعمر|طفق|هاكَ|بخٍ|هاتان|إذ|ثلاثمئة|دون|كأنما|عاد|تِه|واحد|ا|شبه|مهما|ز|علًّ|عشر|لكنما|خ|اثنان|قاف|إليكنّ|أصلا|بعدا|أفريل|من|لكنَّ|هما|قام|ست|ما انفك|ثلاثة|أنًّ|درى|ذاك|نَخْ|آب|أسكن|شتان|إياك|لا|ولو|خمس|ليست|شتانَ|إليكما|يناير|ولكن|هيهات|مازال|هاتين|لكيلا|كليهما|طاق|ر|تجاه|وراءَك|جويلية|هل|أيار|جمعة|تبدّل|ء|تاء|الألى|إياي|تانِ|ذلكن|اثني|آ|صهْ|أضحى|إليكَ|كما|أبٌ|مع|وإذ|فلان|فاء|غداة|تفعلون|ثمانين|أيضا|بغتة|أولالك|لهم|ممن|لات|أبو|ثم|ذواتا|هاته|ها|ثلاث|ؤ|أوّهْ|مساء|لو|فيم

In [18]:
data['text']=data['text'].replace(arab_stopwords, '')
data['text'].tail(10)

40527         الرسم في ناحيه وانا في الناحيه البعيده تماما
46923    جماهير الريال مصيبه نفس اللاعب كانوا يعملوا حف...
19272    اعطي لاداره الاتحاد مليون في عامها الاول لا ما...
37994    ولايه الفقيه ارهاب وقتل الابرياءولادات شعبان س...
22403    بعد ترشيحي من اني احط كل يوم ايه من القران الك...
19857    اعطي لاداره الاتحاد مليون في عامها الاول لا ما...
35485    هل تعرف ماهي الامنيات المستحيله المذكوره في ال...
38772    طريقه الشرح المقدمه في دوره الرسم تاسيس مبادء ...
37805    ابداع في التمثيل وابداع في الترجمه وقد سبقهم ا...
33383    حكومه المملكه عازمه علي تسليم اثنين من اهلنا ا...
Name: text, dtype: object

In [19]:
from nltk.stem.isri import ISRIStemmer
st = ISRIStemmer()

for a in range(len(data['text'])):
    token = word_tokenize(data['text'][a])
    print(token)
    string = []
    for i in token:
        stemmed = st.stem(i)
        string.append(stemmed)
    fstring = ' '.join(string)
    data['text'][a] = fstring
    print(data['text'][a])

Streaming output truncated to the last 5000 lines.
['تعكس', 'المراسيم', 'الرءيه', 'الاقتصاديه', 'المتفرده', 'لصاحب', 'السمو', 'الشيخ', 'محمد', 'بن', 'راشد', 'ال', 'مكتوم', 'لتلبيه', 'متطلبات', 'المرحله', 'الحاليه', 'وال']
عكس مراسيم رءه اقتصاديه تفرد صحب سمو شيخ حمد بن رشد ال كتم تلب تطلب رحل حلي وال
['شركه', 'كشف', 'تسربات', 'المياه', 'بالرياض', 'بالقصيم', 'تمثل', 'الحل', 'الامثل', 'لاصلاح', 'كل', 'مشاكل', 'التسربات', 'نهاءيا', 'دون', 'تكسير', 'وباقل', 'الاسعار', 'وبالضمان']
شرك كشف سرب ياه ريض قصم مثل لحل مثل صلح كل شكل سرب نهء دون كسر بقل سعر لضم
['محلات', 'شراءاثاثمستعملشراء', 'الاثاث', 'المستعمل', 'شراء', 'اثاث', 'مستعمل', 'بالرياض', 'الاثاثالمستعمل', 'بجميع', 'انواعه', 'بالرياض', 'محلاتشراء']
محل شراءاثاثمستعملشراء اثث عمل شرء اثث عمل ريض اثاثالمستعمل جمع واع ريض محلاتشراء
['شركه', 'كشف', 'تسربات', 'المياه', 'بالرياض', 'بالقصيم', 'تمثل', 'الحل', 'الامثل', 'لاصلاح', 'كل', 'مشاكل', 'التسربات', 'نهاءيا', 'دون', 'تكسير', 'وباقل', 'الاسعار', 'وبالضمان']
شرك كشف سرب ياه ريض قصم مثل لحل

In [20]:
data.head(5)

Unnamed: 0  Unnamed: 0.1  \
36557       36557         36557   
566           566           566   
42845       42845         42845   
886           886           886   
17037       17037         17037   

                                                    text   Username  \
36557  لو وسق حفظ في قلد حفظ فيه اول دقق و عشر ثني من...   bodour69   
566    عجل نسب اليوم وطن ال ملك حكم صرف الف ريل لكل و...      J7tm_   
42845            فان كون ادل وتش يقل يفق علي صنع وسق كمل  OreoBAEKY   
886    صرح كثر فعل قلل عجب لمن طلب طبق قان وهو لا طبق...     mkg_12   
17037  شرف عري امن لجن لمب عمرو ادب لا وزر ريض ولا قض...  AtefAbd73   

                            Timestamp  followers  label categorie  
36557  Thu Oct 08 21:30:06 +0000 2020        130      3       art  
566    Sat Oct 10 21:07:25 +0000 2020      35308      1   politic  
42845  Tue Oct 13 16:13:22 +0000 2020        167      3       art  
886    Fri Oct 09 21:50:10 +0000 2020       4277      1   politic  
17037  Fri Oct 09 20:47:27 +0000 2020       2164      0     sport

In [21]:
from sklearn.feature_extraction.text import TfidfVectorizer
unigram_word_vectorizer = TfidfVectorizer(sublinear_tf=True, strip_accents='unicode', analyzer='word', ngram_range=(1, 1), max_features=10000)

In [22]:
unigramdata = unigram_word_vectorizer.fit_transform(data['text'].astype('str'))
unigramdata = unigramdata.toarray()

vocab = unigram_word_vectorizer.get_feature_names()
unigrams = pd.DataFrame(np.round(unigramdata, 1), columns=vocab)
unigrams[unigrams > 0] = 1

unigrams.head()

ءات  ءبف  ءثث  ءثر  ءجد  ءجر  ءخذ  ءخر  ءدب  ءدع  ...  يومياصدقه  \
0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...        0.0   
1  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...        0.0   
2  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...        0.0   
3  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...        0.0   
4  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...        0.0   

   يومياكفيله  يون  يونايتداست  يونغ  يوه  يوي   يي  ييج  ييز  
0         0.0  0.0         0.0   0.0  0.0  0.0  0.0  0.0  0.0  
1         0.0  0.0         0.0   0.0  0.0  0.0  0.0  0.0  0.0  
2         0.0  0.0         0.0   0.0  0.0  0.0  0.0  0.0  0.0  
3         0.0  0.0         0.0   0.0  0.0  0.0  0.0  0.0  0.0  
4         0.0  0.0         0.0   0.0  0.0  0.0  0.0  0.0  0.0  

[5 rows x 10000 columns]

In [23]:
from sklearn import preprocessing

pro = preprocessing.LabelEncoder()
encpro = pro.fit_transform(data['categorie'])
data['categorie'] = encpro
y = data['categorie']

In [24]:
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(unigrams, y,test_size=0.2)
print('Training Data:', X_train.shape[0])
print('Test Data:', X_test.shape[0])

Training Data: 37666
Test Data: 9417


In [36]:
X_train.shape

(37666, 10000)

In [37]:
y_train.shape

(37666,)

In [25]:
from sklearn.svm import LinearSVC
from sklearn.linear_model import LogisticRegression, RidgeClassifier
from sklearn.metrics import precision_score, recall_score

svm = LinearSVC(max_iter=300, multi_class='ovr')
svm = svm.fit(X_train, y_train)

y_pred = svm.predict(X_test)
print('Accuracy= ', svm.score(X_test, y_test)))
print("Precision Score of all classes: ", precision_score(y_test, y_pred, average=None))
print("Recall score of all classes: ", recall_score(y_test, y_pred, average=None))

Accuracy= 0.917
Precision Score :  [0.90640641 0.93889798 0.89468196 0.91403217 0.93297587]
recall_score :  [0.92350841 0.92377885 0.89421574 0.90798898 0.93598709]


In [26]:
LRC = LogisticRegression()
LRC = LRC.fit(X_train, y_train)

y_pred = LRC.predict(X_test)

print('Accuracy : ', LRC.score(X_test, y_test))
print("Precision of all classes: ", precision_score(y_test, y_pred, average=None))
print("Recall of all classes: ", recall_score(y_test, y_pred, average=None))

Accuracy :  0.9225868110863332
Precision of all classes:  [0.90197044 0.94812362 0.90271967 0.92024202 0.94308943]
Recall of all classes:  [0.93370729 0.92216855 0.89942678 0.92176309 0.93598709]


In [33]:
from tensorflow.keras.models import Model, Sequential
from tensorflow.keras.layers import Dense ,Dropout
from tensorflow.keras.optimizers import SGD

In [42]:
unigram_model = Sequential()
unigram_model.add(Dense(128, input_shape=((unigrams.shape)[1],), activation='tanh'))
unigram_model.add(Dropout(0.5))
unigram_model.add(Dense(64, activation='tanh'))
unigram_model.add(Dropout(0.5))
unigram_model.add(Dense(5, activation='softmax'))

sgd = SGD(learning_rate=0.001)
unigram_model.compile(loss='sparse_categorical_crossentropy', optimizer=sgd, metrics=['accuracy'])

#fitting and saving the model 
hist = unigram_model.fit(X_train, y_train, epochs=100, batch_size=32, verbose=1, validation_split=0.2)

Epoch 1/100
942/942 [==============================] - 10s 10ms/step - loss: 1.5759 - accuracy: 0.2942 - val_loss: 1.5153 - val_accuracy: 0.5568
Epoch 2/100
942/942 [==============================] - 9s 10ms/step - loss: 1.4719 - accuracy: 0.4999 - val_loss: 1.4133 - val_accuracy: 0.7061
Epoch 3/100
942/942 [==============================] - 10s 10ms/step - loss: 1.3700 - accuracy: 0.6262 - val_loss: 1.3084 - val_accuracy: 0.7576
Epoch 4/100
942/942 [==============================] - 10s 10ms/step - loss: 1.2656 - accuracy: 0.6955 - val_loss: 1.1997 - val_accuracy: 0.7786
Epoch 5/100
942/942 [==============================] - 10s 10ms/step - loss: 1.1623 - accuracy: 0.7373 - val_loss: 1.0911 - val_accuracy: 0.7913
Epoch 6/100
942/942 [==============================] - 10s 10ms/step - loss: 1.0602 - accuracy: 0.7661 - val_loss: 0.9876 - val_accuracy: 0.8059
Epoch 7/100
942/942 [==============================] - 10s 10ms/step - loss: 0.9641 - accuracy: 0.7841 - val_loss: 0.8939 - val_acc